In [1]:
# Dependencies
import requests
import json
from pprint import pprint
import pandas as pd
import os
import csv
import numpy as np
import time 
import tweepy
from config import consumer_key, consumer_secret, access_token, access_token_secret
from datetime import datetime
import math
import pytz
# Import and Initialize Sentiment Analyzer
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
analyzer = SentimentIntensityAnalyzer()

utc=pytz.UTC
startDate = datetime(2018, 1, 1, 0, 0, 0)
endDate = datetime(2018, 4, 10, 0, 0, 0)
startDate = utc.localize(startDate) 
endDate = utc.localize(endDate) 

In [3]:
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token, access_token_secret)

path2 = "resources/LocalTV_Twitter.csv"
df_TV_raw = pd.read_csv(path2, encoding = "latin1")

df_TV_raw = df_TV_raw[df_TV_raw['TwitterHandle'] != 'None']

print(df_TV_raw.count())
df_TV=df_TV_raw.drop_duplicates(subset= ["TwitterHandle"])
print(df_TV.count())

df_tweet = pd.DataFrame(data=df_TV)
df_tweet.head()

TwitterHandle    589
City             589
StateAbrr        589
dtype: int64
TwitterHandle    578
City             578
StateAbrr        578
dtype: int64


TwitterHandle        City StateAbrr
0           @KMSSTV  Shreveport        LA
1             @kvoa      Tucson        AZ
2      @FaceofFox43     Norfolk        VA
3      @thewbdotcom     Burbank        CA
4  @GulfCoastCWCreW      Mobile        AL

In [8]:
# "Real Person" Filters
min_tweets = 5
max_tweets = 500000
max_followers = 20000
max_following = 20000
lang = "en"


# Set other parameters
api = tweepy.API(auth, wait_on_rate_limit=True, wait_on_rate_limit_notify= True, parser=tweepy.parsers.JSONParser())
entry = 0
unique_ids = []
oldest_tweet = None
output_list = pd.DataFrame(columns=['created_at','account_location','text_tweet', 'name'])
output_list_final = pd.DataFrame()

In [10]:
# Super Twitter Loop
for (idx, row) in df_tweet.iterrows():
    #entry += 1 
    user_name = (row.loc['TwitterHandle'])
    # Loop through each user
    counter = 0
    # Loop through pages.
    for x in range(30):
        try:
            # Get all tweets from home feed
            public_tweets = api.user_timeline(user_name, page=x, tweet_mode="extended", count=100)
            # Loop through all tweets
            for tweet in public_tweets:
            #Use filters to check if user meets conditions
                if (tweet['user']["followers_count"] < max_followers and
                    tweet['user']["statuses_count"] > min_tweets and
                    tweet['user']["statuses_count"] < max_tweets and
                    tweet['user']["friends_count"] < max_following and
                    tweet["lang"] == lang):
            #Read information
                        created_at= tweet['created_at']
                        created_at =datetime.strptime(created_at, "%a %b %d %H:%M:%S %z %Y")
                        name = tweet['user']['screen_name']                            
                        pprint(created_at)
                        account_location = tweet['user']["location"]
                        pprint(account_location)
                        text_tweet = tweet["full_text"]
                        pprint(text_tweet)
                        output_list.at[idx, 'created_at'] = created_at
                        output_list.at[idx, 'text_tweet'] = text_tweet
                        output_list.at[idx, 'account_location'] = account_location
                        output_list.at[idx, 'name'] = name
                        output_list_final = output_list.append(output_list)
        except Exception as e:
            print(e)
            time.sleep(5)
            print("restarting...")
            pass

datetime.datetime(2018, 4, 20, 4, 12, 45, tzinfo=datetime.timezone.utc)
'Shreveport, LA'
('RT @TimONBC6: VIDEO: Mudbugs fall short in closeout game, drop game 3 at '
 'Corpus Christi\n'
 'Story- https://t.co/jn9PldBegz\n'
 '#ktalhockey \n'
 'Game-4…')
datetime.datetime(2018, 4, 20, 3, 4, 30, tzinfo=datetime.timezone.utc)
'Shreveport, LA'
('RT @TimONBC6: The Corpus Christi IceRays force a game four, topping the '
 'Mudbugs tonight 5-1. Highlights and post game reaction from tonight…')
datetime.datetime(2018, 4, 20, 1, 0, 2, tzinfo=datetime.timezone.utc)
'Shreveport, LA'
('UIL to use instant replay at all Texas HS football state championship games '
 'starting in 2018 https://t.co/Ijq89P6G4B')
datetime.datetime(2018, 4, 19, 17, 39, 38, tzinfo=datetime.timezone.utc)
'Shreveport, LA'
"BREAKING: No criminal charges filed in Prince's death. https://t.co/wiH0bvRnWh"
datetime.datetime(2018, 4, 19, 12, 0, 20, tzinfo=datetime.timezone.utc)
'Shreveport, LA'
('Life as a #military kid has taken thi

KeyboardInterrupt: 

In [47]:
output_list_final.head(200)
output_list_final.to_csv('resources/TV_Tweets.csv')

path2 = "resources/TV_Tweets.csv"
df_TV_raw = pd.read_csv(path2, encoding = "latin1")

created_at  account_location  \
0  2016-05-31 20:49:30+00:00  Jacksonville, AL   
1  2018-01-15 17:05:09+00:00           Alabama   

                                          text_tweet           name  
0  Our last account kept getting hacked so we had...       WLJS_919  
1  You'll hear Danny Glover tomorrow on APR for t...  ALPublicRadio

In [13]:
# Run Vader Analysis on each tweet
for (idx, row) in output_list.iterrows():
    text = (row.loc['text_tweet'])
    counter += 1
    results = analyzer.polarity_scores(text)
    compound = results["compound"]
    pos = results["pos"]
    neu = results["neu"]
    neg = results["neg"]
    tweet_times.append(tweet["created_at"])
    output_list.at[idx, 'compound'] = compound
    output_list.at[idx, 'pos'] = pos
    output_list.at[idx, 'neu'] = neu
    output_list.at[idx, 'neg'] = neg


In [18]:
output_list['text_tweet'] = output_list['text_tweet'].str.lower()
place = output_list.copy
place

<bound method NDFrame.copy of                   created_at account_location  \
0  2018-04-12 03:13:14+00:00   Shreveport, LA   

                                          text_tweet    name  compound    pos  \
0  rt @ktalsports: video - the mudbugs' mindset i...  KMSSTV    0.3612  0.152   

     neu  neg  
0  0.848  0.0  >